# 1D FD Forward and Adjoint Wave Propagation

This little notebook implements frequency-domain wave propagation in 1D using second-order finite differences in space. It includes the solution of the forward problem and the adjoint-based computation of a misfit gradient. In contrast to the classical parameterisation in terms of real and imaginary velocity, this version uses logarithmic velocities. As a consequence, there is no change in an inverse problem solution when transforming from velocity to the equally justified slowness.


**copyright**: Andreas Fichtner (andreas.fichtner@erdw.ethz.ch), December 2020,

**license**: BSD 3-Clause (\"BSD New\" or \"BSD Simplified\")

## 0. Python packages

In [ ]:
import numpy as np
import scipy.sparse as sp
import scipy.sparse.linalg as sla
import matplotlib.pyplot as plt

plt.rcParams["font.family"] = "Times"
plt.rcParams.update({'font.size': 50})
plt.rcParams['xtick.major.pad']='12'
plt.rcParams['ytick.major.pad']='12'

## 1. Input

Our simulations need only a small number of input parameters: the total number of grid points along the line (n), the spacing between these grid points (dx), the frequency of the monochromatic waves (f), the grid point indices where the sources are located (ns), and the grid point indices where we make the measurements (rix).

In [ ]:
# Number of grid points.
n=1000
# Space increment [m].
dx=1000.0
# Frequencies [Hz].
f=[0.02,0.04,0.08,0.16,0.32]
# Indices of point source locations.
ns=[90,120,300,330,360,400,800,850,900]
# Measurement indices (receiver locations).
rix=[50,51,52,53,54,55,56,57,58,59,60,150,151,152,153,154,155,156,157,158,159,160,650,651,652,653,654,655,656,657,658,659,660]

# Reference velocities.
cr_ref=3000.0
ci_ref=40.0

# A priori standard deviation of the data error.
sigma_d=1.0

# A priori standard deviations of real and imaginary velocities.
sigma_vr=0.2*1000.0
sigma_vi=2.0*1000.0

# Number of all measurements.
Nall=np.float(len(rix)*len(f)*len(ns))

## 2. Initialisations

We need to initialise various field variables, namely the true velocity distribution that one may want to recover (c_obs), the initial velocity distribution (c), and the spatial distribution of the sources (s).

In [ ]:
# Types of models.
model_type='boxes1'

# Make and plot velocity distribution [m/s].
x=np.arange(0.0,n*dx,dx)

if model_type=='spike':
    c_log=np.log(3000.0*np.ones(n,dtype=np.cfloat)/cr_ref)+1.0j*np.log(40.0/ci_ref)
    c_log_obs=np.log(3000.0*np.ones(n,dtype=np.cfloat)/cr_ref)+1.0j*np.log(40.0/ci_ref)
    c_log_obs[520]=np.log(4000.0/cr_ref)+1.0j*np.log(30.0/ci_ref)

elif model_type=='boxes1':
    c_log_obs=np.log(3000.0*np.ones(n,dtype=np.cfloat)/cr_ref)+1.0j*np.log(40.0/ci_ref)
    c_log_obs[30:100]=np.log(2000.0/cr_ref)+1.0j*np.log(60.0/ci_ref)
    c_log_obs[150:200]=np.log(3500.0/cr_ref)+1.0j*np.log(10.0/ci_ref)
    c_log_obs[200:400]=np.log(2500.0/cr_ref)+1.0j*np.log(40.0/ci_ref)
    c_log_obs[450:600]=np.log(2200.0/cr_ref)+1.0j*np.log(100.0/ci_ref)
    c_log_obs[700:850]=np.log(4000.0/cr_ref)+1.0j*np.log(10.0/ci_ref)
    
    c_log=0.8*c_log_obs.copy()
    for i in range(100):
        c_log[1:n-1]=(c_log[0:n-2]+c_log[2:n]+c_log[1:n-1])/3.0
        
elif model_type=='boxes2':
    c_log_obs=np.log(3000.0*np.ones(n,dtype=np.cfloat)/cr_ref)+1.0j*np.log(10.0/ci_ref)
    c_log_obs[300:350]=np.log(2500.0/cr_ref)+1.0j*np.log(20.0/ci_ref)
    
    c_log=c_log_obs.copy()
    for i in range(100):
        c_log[1:n-1]=(c_log[0:n-2]+c_log[2:n]+c_log[1:n-1])/3.0
    

# Plot models.
plt.subplots(1,figsize=(30,10))
plt.plot(x/1000.0,np.real(c_log_obs),'k',LineWidth=3)
plt.plot(x/1000.0,np.real(c_log),'r',LineWidth=3)
scale=1.1*np.max(np.abs(np.real(c_log_obs)))
plt.xlabel('x [km]')
plt.ylabel('c_re [1]')
plt.ylim(-scale,scale)
plt.xlim([x[0]/1000.0,x[-1]/1000.0])
plt.grid()
plt.title('real logarithmic velocity distribution (black=true, red=initial)',pad=20)
plt.savefig('OUTPUT_forward/velocity_real.png',bbox_inches='tight',format='png')
plt.show()

plt.subplots(1,figsize=(30,10))
plt.plot(x/1000.0,np.imag(c_log_obs),'k',LineWidth=3)
plt.plot(x/1000.0,np.imag(c_log),'r',LineWidth=3)
scale=1.1*np.max(np.abs(np.imag(c_log_obs)))
plt.xlabel('x [m]')
plt.ylabel('c_im [1]')
plt.ylim(-scale,scale)
plt.xlim([x[0]/1000.0,x[-1]/1000.0])
plt.grid()
plt.title('imaginary logarithmic velocity distribution (black=true, red=initial)',pad=20)
plt.savefig('OUTPUT_forward/velocity_imag.png',bbox_inches='tight',format='png')
plt.show()

# Wavelength and number of grid points per wavelength.
lambda_min=np.min(cr_ref*np.exp(np.real(c_log)))/np.max(f)
lambda_max=np.max(cr_ref*np.exp(np.real(c_log)))/np.max(f)
gppmw=lambda_min/dx

print('minimum wavelength: %f m' % lambda_min)
print('maximum wavelength: %f m' % lambda_max)
print('grid points per minimum wavelength: %f' % gppmw)

## 3. Forward problem solution

We solve the forward problem using second-order central finite differences in space. Hence, the impedance matrix $\mathbf{L}$ is defined through its action on the discrete wavefield $\mathbf{u}$ as
\begin{equation}
L_{ij}u_j = \omega^2 u_i + \frac{c_i^2}{dx^2} [u_{i+1}-2u_i+u_{i-1}]\,.
\end{equation}
The complete discrete system is then
\begin{equation}
\mathbf{Lu}=-\mathbf{s}\,.
\end{equation}
Numerically, we solve the problem with a sparse LU decomposition. This would allow us to quickly solve the problem for many different sources. $$ $$

In [ ]:
def forward(n,dx,c_log,ns,f):
    """
    Forward problem solution via LU decomposition.
    :param n: number of grid points
    :param dx: spatial finite-difference increment
    :param c: logarithmic velocity distribution of dimension n
    :param ns: number of sources
    :param f: frequency vector
    """
    
    # Compute actual velocities.
    c=cr_ref*np.exp(np.real(c_log))+1.0j*ci_ref*np.exp(np.imag(c_log))
    
    # Initialise displacement vector.
    u=np.zeros((n,len(ns),len(f)),dtype=np.cfloat)
    
    # March through frequencies.
    for nf in range(len(f)):
    
        # Diagonal offsets.
        offsets=np.array([0,1,-1])
        # Initialise (sub)diagonal entries.
        data=np.zeros((3,n),dtype=np.cfloat)
        data[0,:]=-2.0*(c**2)/(dx**2)+(2.0*np.pi*f[nf])**2
        data[1,:]=np.roll(c**2,1)/(dx**2)
        data[2,:]=np.roll(c**2,-1)/(dx**2)
        # Make impedance matrix.
        L=sp.dia_matrix((data, offsets),shape=(n, n),dtype=np.cfloat)
    
        # Make sparse LU decomposition.
        lu=sla.splu(L.tocsc())
    
        # March through sources.
        for i in range(len(ns)):
            # Make ith point source. Scale with large number to avoid underflow and with frequency to ensure similar amplitudes.
            s=np.zeros(n,dtype=np.cfloat)
            s[ns[i]]=1.0e5*f[nf]/dx
            # Solve linear system.
            u[:,i,nf]=lu.solve(-s)
    
    # Return.
    return u

In [ ]:
# Compute wavefields for true and for initial velocity distributions.
u=forward(n,dx,c_log,ns,f)

np.random.seed(1)
u_obs=forward(n,dx,c_log_obs,ns,f)+sigma_d*np.random.randn(n,len(ns),len(f))

# Plot the wavefields.
for j in range(len(f)):
    for i in range(len(ns)):
        plt.subplots(1,figsize=(30,10))
        plt.plot(x/1000.0,np.real(u_obs[:,i,j].reshape(np.shape(x))),'k',LineWidth=3)
        plt.plot(x/1000.0,np.real(u[:,i,j].reshape(np.shape(x))),'r',LineWidth=3)
        plt.plot(x[ns]/1000.0,np.zeros(len(ns)),'*',markerfacecolor=[0.7,0.7,1.0],markersize=30,markeredgecolor='k',markeredgewidth=2)
        plt.plot(x[ns[i]]/1000.0,0.0,'*',markerfacecolor=[0.5,0.5,1.0],markersize=60,markeredgecolor='k',markeredgewidth=2)
        plt.plot(x[rix]/1000.0,np.real(u_obs[rix,i,j]),'^',markerfacecolor=[1.0,0.5,0.5],markersize=30,markeredgecolor='k',markeredgewidth=2)
        plt.xlim([x[0]/1000.0,x[-1]/1000.0])
        plt.xlabel('x [km]')
        plt.ylabel('u [m*s]')
        plt.grid()
        plt.title('wavefield for source %d and frequency %f Hz' % (i,f[j]),pad=20)
        fn='OUTPUT_forward/wavefield_'+str(i)+'_'+str(j)+'.png'
        plt.savefig(fn,bbox_inches='tight',format='png')
        plt.show()

## 4. Misfit and adjoint problem

To measure the difference between the wavefields $u$ and $u^{obs}$ at the receiver locations, we define a simple $L_2$ misfit
\begin{equation}
\chi = \frac{1}{2} \sum_f \sum_r [u_r(f) - u_r^{obs}(f)]^2\,,
\end{equation}
where the sum is over all receiver indices and frequencies. The corresponding adjoint source has the non-zero entries
\begin{equation}
s_r^* = \frac{1}{2} (u_r^{obs} - u_r)\,.
\end{equation}
The impedance matrix of the adjoint problem is the Hermetian conjugate of $\mathbf{L}$.

In [ ]:
def U(u,u_obs,c_log):
    
    # Compute L2 misfit.
    return 0.5*np.sum(np.abs(u[rix,:,:]-u_obs[rix,:,:])**2)/(Nall*sigma_d**2)+0.5*np.sum(np.real(c_log)**2)/(n*sigma_vr**2)+0.5*np.sum(np.imag(c_log)**2)/(n*sigma_vi**2)

chi=U(u,u_obs,c_log)
print('misfit: %g' % chi)

In [ ]:
def adjoint(n,dx,c_log,s,f):
    """
    Forward problem solution via LU decomposition.
    :param n: number of grid points
    :param dx: spatial finite-difference increment
    :param c: logarithmic velocity distribution of dimension n
    :param s: adjoint source of dimension n
    :param f: frequency [Hz]
    """
    
    # Compute actual velocities.
    c=cr_ref*np.exp(np.real(c_log))+1.0j*ci_ref*np.exp(np.imag(c_log))
    
    # Diagonal offsets.
    offsets=np.array([0,1,-1])
    # Initialise (sub)diagonal entries.
    data=np.zeros((3,n),dtype=np.cfloat)
    data[0,:]=np.conj(-2.0*(c**2)/(dx**2)+(2.0*np.pi*f)**2)
    data[1,:]=np.conj(np.roll(c**2,1)/(dx**2))
    data[2,:]=np.conj(np.roll(c**2,-1)/(dx**2))
    # Make impedance matrix.
    L=sp.dia_matrix((data,offsets),shape=(n, n),dtype=np.cfloat)
    
    # Solve via sparse LU decomposition.
    lu=sla.splu(L.transpose().tocsc())
    v=lu.solve(-s)
    
    # Return.
    return v

## 5. Compute gradient

We finally compute the discrete gradient, the components of which are given as
\begin{equation}
\frac{\partial\chi}{\partial c_i^{(r)}} = 4 Re\, c_i v_i^* e_i\,,
\end{equation}
and
\begin{equation}
\frac{\partial\chi}{\partial c_i^{(i)}} = -4 Im\, c_i v_i^* e_i\,,
\end{equation}
where $e_i$ is the discrete second derivative of the forward wavefield
\begin{equation}
e_i = \frac{1}{dx^2} [u_{i+1} - 2u_i + u_{i-1}]\,.
\end{equation}

In [ ]:
# Derivative with respect to real part of logarithmic velocity c.
dchi_r=np.zeros(n,dtype=np.cfloat)
# Derivative with respect to imaginary part of logarithmic velocity c.
dchi_i=np.zeros(n,dtype=np.cfloat)

# Compute actual velocities.
c=cr_ref*np.exp(np.real(c_log))+1.0j*ci_ref*np.exp(np.imag(c_log))

# Accumulate gradient by marching through frequencies and sources.
for j in range(len(f)):
    for i in range(len(ns)):
        # Make adjoint source.
        sa=np.zeros(n,dtype=np.cfloat)
        sa[rix]=0.5*(u[rix,i,j]-u_obs[rix,i,j])
        # Solve adjoint problem.
        v=adjoint(n,dx,c_log,sa,f[j])
        # Add to gradient.
        e=np.zeros(n,dtype=np.cfloat)
        e[1:n-1]=(u[0:n-2,i,j]-2.0*u[1:n-1,i,j]+u[2:n,i,j])/(dx**2)
        # Compute gradients.
        dchi_r+=4.0*np.real(c*np.conj(v)*e)*np.real(c)
        dchi_i-=4.0*np.imag(c*np.conj(v)*e)*np.imag(c)
        
# Include scaling and add a priori term.
dchi_r=dchi_r/(Nall*sigma_d**2)+np.real(c_log)/(n*sigma_vr**2)
dchi_i=dchi_i/(Nall*sigma_d**2)+np.imag(c_log)/(n*sigma_vi**2)

In [ ]:
# Plot.
plt.subplots(1,figsize=(30,20))
plt.plot(x,np.real(dchi_r))
plt.xlabel('x [m]')
plt.ylabel('misfit gradient')
#plt.xlim([0,0.2e6])
plt.grid()
plt.title('derivative with respect to real part')
plt.show()

plt.subplots(1,figsize=(30,20))
plt.plot(x,np.real(dchi_i))
plt.xlabel('x [m]')
plt.ylabel('misfit gradient')
plt.grid()
plt.title('derivative with respect to imaginary part')
plt.show()

## 7. Gradient tests

### 7.1. Hockey stick test

The hockey stick test compares the adjoint-derived derivative with a finite-difference approximation of the derivative. In general, we expect this difference to be small. However, the difference will increase when the finite-difference increment is too large (poor finite-difference approximation) and when it is too small (floating point inaccuracy). This produces a characteristic hockey stick plot.

#### 7.1.1. Real part of velocity

In [ ]:
# Index of the model parameter.
idx=100
# Range of model perturbation.
dc_log=(10.0**np.arange(-10.0,4.0,1.0))/cr_ref

# Initialise arrays.
dchi_fd=np.zeros(len(dc_log))
c1_log=np.zeros(n,dtype=np.cfloat)
c2_log=np.zeros(n,dtype=np.cfloat)
c1_log[:]=c_log[:]
c2_log[:]=c_log[:]

# March through perturbation ranges.
for i in range(len(dc_log)):
    # Positive and negative model perturbations.
    c1_log[idx]=c_log[idx]+dc_log[i]
    c2_log[idx]=c_log[idx]-dc_log[i]
    # Solve forward problems.
    u1=forward(n,dx,c1_log,ns,f)
    u2=forward(n,dx,c2_log,ns,f)
    # Finite-difference approximation of derivative.
    dchi_fd[i]=U(u1,u_obs,c1_log)-U(u2,u_obs,c2_log)
    dchi_fd[i]=dchi_fd[i]/(2.0*dc_log[i])    

In [ ]:
plt.loglog(dc_log,np.abs((dchi_fd-dchi_r[idx])/dchi_r[idx]))
plt.loglog(dc_log,np.abs((dchi_fd-dchi_r[idx])/dchi_r[idx]),'ko')
plt.xlabel('finite-difference increment dc')
plt.ylabel('relative derivative error')
plt.title('hockey stick plot')
plt.show()

#### 7.1.2. Imaginary part of velocity

In [ ]:
# Index of the model parameter.
idx=50
# Range of model perturbation.
dc_log=(10.0**np.arange(-10.0,4.0,1.0))/ci_ref

# Initialise arrays.
dchi_fd=np.zeros(len(dc_log))
c1_log=np.zeros(n,dtype=np.cfloat)
c2_log=np.zeros(n,dtype=np.cfloat)
c1_log[:]=c_log[:]
c2_log[:]=c_log[:]

# March through perturbation ranges.
for i in range(len(dc_log)):
    # Positive and negative model perturbations.
    c1_log[idx]=c_log[idx]+1j*dc_log[i]
    c2_log[idx]=c_log[idx]-1j*dc_log[i]
    # Solve forward problems.
    u1=forward(n,dx,c1_log,ns,f)
    u2=forward(n,dx,c2_log,ns,f)
    # Finite-difference approximation of derivative.
    dchi_fd[i]=U(u1,u_obs,c1_log)-U(u2,u_obs,c2_log)
    dchi_fd[i]=dchi_fd[i]/(2.0*dc_log[i])

In [ ]:
plt.loglog(dc_log,np.abs((dchi_fd-dchi_i[idx])/dchi_i[idx]))
plt.loglog(dc_log,np.abs((dchi_fd-dchi_i[idx])/dchi_i[idx]),'ko')
plt.xlabel('finite-difference increment dc')
plt.ylabel('relative derivative error')
plt.title('hockey stick plot')
plt.show()

### 7.2. Space-dependent derivative

For a fixed finite-difference increment, we may also compute a finite-difference approximation of the misfit derivative for all grid points and compare this to the adjoint-based derivative. This is precisely the brute-force approach that adjoint methods are supposed to avoid.

#### 7.2.1. Real part of velocity

In [ ]:
# Fixed finite-difference increment.
dc_log=1.0e-6

# Initialise arrays.
dchi_fd=np.zeros(n)
c1_log=np.zeros(n,dtype=np.cfloat)
c2_log=np.zeros(n,dtype=np.cfloat)

# March through grid points.
for i in range(n):
    # Positive and negative model perturbations.
    c1_log[:]=c_log[:]
    c2_log[:]=c_log[:]
    c1_log[i]=c_log[i]+dc_log
    c2_log[i]=c_log[i]-dc_log
    # Solve forward problems.
    u1=forward(n,dx,c1_log,ns,f)
    u2=forward(n,dx,c2_log,ns,f)
    # Finite-difference approximation of derivative.
    dchi_fd[i]=U(u1,u_obs,c1_log)-U(u2,u_obs,c2_log)
    dchi_fd[i]=dchi_fd[i]/(2.0*dc_log)

In [ ]:
plt.plot(x,dchi_fd)
plt.xlabel('x [m]')
plt.ylabel('misfit gradient (FD)')
plt.title('FD approximation of misfit gradient')
plt.show()

plt.semilogy(x,np.abs(dchi_fd-dchi_r))
plt.xlabel('x [m]')
plt.ylabel('misfit gradient (FD)')
plt.title('error of FD approximation')
plt.show()

#### 7.1.2. Imaginary part of velocity

In [ ]:
# Fixed finite-difference increment.
dc_log=1.0e-2/cr_ref

# Initialise arrays.
dchi_fd=np.zeros(n)
c1_log=np.zeros(n,dtype=np.cfloat)
c2_log=np.zeros(n,dtype=np.cfloat)

# March through grid points.
for i in range(n):
    # Positive and negative model perturbations.
    c1_log[:]=c_log[:]
    c2_log[:]=c_log[:]
    c1_log[i]=c_log[i]+1j*dc_log
    c2_log[i]=c_log[i]-1j*dc_log
    # Solve forward problems.
    u1=forward(n,dx,c1_log,ns,f)
    u2=forward(n,dx,c2_log,ns,f)
    # Finite-difference approximation of derivative.
    dchi_fd[i]=U(u1,u_obs,c1_log)-U(u2,u_obs,c2_log)
    dchi_fd[i]=dchi_fd[i]/(2.0*dc_log)

In [ ]:
plt.plot(x,dchi_fd)
plt.xlabel('x [m]')
plt.ylabel('misfit gradient (FD)')
plt.title('FD approximation of misfit gradient')
plt.show()

plt.semilogy(x,np.abs(dchi_fd-dchi_i))
plt.xlabel('x [m]')
plt.ylabel('misfit gradient (FD)')
plt.title('error of FD approximation')
plt.show()